In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import tensorflow as tf
from tensorflow.keras import layers, optimizers, callbacks
import time
import itertools

from multiprocessing import Pool, Process, cpu_count
#from plot_efficient_frontier import plot_frontier_carlos as plot_frontier
import numpy as np
from auxiliary_functions import *

from life_cycle_gradient_descent import optimize

In [3]:
import plotly
import plotly.graph_objs as go
from ipywidgets import widgets

In [29]:
def init_tf_model(NN_structure = [300,300, 300]):
    # model inputs
    inputs = tf.keras.Input(shape=(3,))
    activation_function = 'relu'

    # first layer after inputs
    x = layers.Dense(NN_structure[0], activation=activation_function)(inputs)
    # build hidden layers
    for nodes_in_layer in NN_structure[1:]:
        x = layers.Dense(nodes_in_layer, activation=activation_function)(x)
    # output layer
    prediction = layers.Dense(2, activation='linear')(x)

    model = tf.keras.Model(inputs=inputs, outputs=prediction)

    # The compile step specifies the training configuration.
    model.compile(optimizer=tf.keras.optimizers.Adam(lr=0.001,clipnorm=1.),
                  loss='mse',
                  metrics=['mae', 'accuracy'])

    return model

In [30]:
def fit_model(model, data_x, data_y):
    # define callbacks to be executed during training
    checkpoints = callbacks.ModelCheckpoint("checkpoint_model.h5", monitor='val_loss', verbose=0, save_best_only=True,
                                            save_weights_only=False, mode='auto', period=1000)

    tensorboard = callbacks.TensorBoard(log_dir='./tensorboard_data', histogram_freq=100, batch_size=32,
                                        write_graph=True, write_grads=False, write_images=True,
                                        embeddings_freq=0, embeddings_layer_names=None,
                                        embeddings_metadata=None, embeddings_data=None, update_freq='epoch')

    early_stopping = callbacks.EarlyStopping(monitor='val_loss', min_delta=1E-4, patience=200, verbose=0,
                                             mode='min', baseline=None, restore_best_weights=False)

    callback_list = [checkpoints, tensorboard, early_stopping]

    model.fit(data_x, data_y, batch_size=len(data_x), epochs=20000,
              validation_split=0.15, shuffle=True, verbose=1)

    model.save("trained_model.h5")


    return model

In [8]:
conf = {
    'tax_setting': 5,  # tax setting: see below for detailed explanation
    'beta': 0.95,  # Utility discounting
    'r_debt': 0.15,  # debt interest rate
    'r': 0.1,
    'T': 60,  # agent's maturity
    'T_ret': 45,  # retirement age
    'L_max': 10,  # maximum labour
    'gamma': 0.5,  # Agent's utility from consumption
    'eta': 8,  # Agent's disutility from labour
    'plot': False,
    'plot_steps': False,
    'plot_GD_steps': False,
    'h': 1E-6,  # step size finite difference
    'n_steps_max': 100,  # max number of steps for 1 point on pareto frontier
    'k_max': 100,  # max number of steps for bi-linear search
    'tol': 1E-3,  # tolerance for gradient stopping
    'tol_line_search': 1E-8,  # tolerance to abort line search
    'serial': False,
    'max_debt': 2,
    'costb': 0.02,
    'borrowing': np.inf,  # np.inf -> allow unlimited borrowing // 0 -> allow no borrowing
    'n_starting_points': 150  # number of starting points for "frontier searching"
}
timestr = time.strftime("%m-%d-%H%M")

# extract parameters from configuration dictionary
gamma = conf["gamma"]
eta = conf["eta"]
n_points = conf["n_starting_points"]
r = conf["r"]
T = conf["T"]

# build interest rate vector of length
r = np.full(T, r)

# set n_procs
n_procs = cpu_count() - 1
#    n_procs = 1 

# create gamma eta pairs from input
#gammas_etas = itertools.product(gamma, eta)

# n points per process
n = n_points // n_procs
wage = wage_function(conf)

# initialize NLP problem - S = casadi optimization object - lb_x ub_x are the lower and upper bounds
S, lb_x, ub_x = init_optimization_problem(r, wage, conf)

-------------------------------------------
This is casadi::QRQP
Number of variables:                             302
Number of constraints:                           120
Number of nonzeros in H:                         120
Number of nonzeros in A:                         465
Number of nonzeros in KKT:                      1352
Number of nonzeros in QR(V):                    1214
Number of nonzeros in QR(R):                    2242


In [20]:
    interval_grid = np.random.rand(20000, 3)

    #grid = np.array(list(itertools.product(interval_grid, interval_grid, interval_grid)))
    data_x = []
    
    results = []
    x0 = 1
    lam_x0 = 0
    lam_g0 = 0
    for i, tax_policy in enumerate(interval_grid):
        try:
            util, revenue, _,  x0, lam_x0, lam_g0 = optimize(lb_x, ub_x, S, tax_policy, wage, r, conf, x0, lam_x0, lam_g0)
            if S[1].stats()["success"]:
                data_x.append(tax_policy)
                results.append([util, revenue])
            else:
                continue
        except:
            continue
    data_x = np.array(data_x)
    data_y = np.array(results)


CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_jac_fg failed: Inf detected for output grad_f_x, at (row 57, col 0).") [.../casadi/core/oracl

...

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.cpp:249]
CasADi -  WARNING("S:nlp_fg failed: NaN detected for output f, at (row 0, col 0).") [.../casadi/core/oracle_function.c

In [31]:
model = init_tf_model()

In [34]:
fit_model(model, data_x, data_y)

Train on 16594 samples, validate on 2929 samples
Epoch 1/20000
16594/16594 [==============================] - 0s 5us/sample - loss: 446.4266 - mean_absolute_error: 6.3100 - acc: 0.8761 - val_loss: 1129279.5000 - val_mean_absolute_error: 16.9817 - val_acc: 0.9454
Epoch 2/20000
16594/16594 [==============================] - 0s 6us/sample - loss: 378.0566 - mean_absolute_error: 2.8572 - acc: 0.9476 - val_loss: 1129788.2500 - val_mean_absolute_error: 19.8928 - val_acc: 0.8549
Epoch 3/20000
16594/16594 [==============================] - 0s 4us/sample - loss: 437.9496 - mean_absolute_error: 5.8939 - acc: 0.8480 - val_loss: 1130000.5000 - val_mean_absolute_error: 22.1479 - val_acc: 0.7825
Epoch 4/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 506.2312 - mean_absolute_error: 8.1729 - acc: 0.7763 - val_loss: 1129789.1250 - val_mean_absolute_error: 19.4930 - val_acc: 0.8638
Epoch 5/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 422.8027 - m

Epoch 39/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 414.2789 - mean_absolute_error: 5.6130 - acc: 0.8372 - val_loss: 1129986.5000 - val_mean_absolute_error: 21.4912 - val_acc: 0.7839
Epoch 40/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 475.3739 - mean_absolute_error: 7.5042 - acc: 0.7783 - val_loss: 1129724.0000 - val_mean_absolute_error: 18.4746 - val_acc: 0.8846
Epoch 41/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 398.8431 - mean_absolute_error: 4.4567 - acc: 0.8790 - val_loss: 1129269.2500 - val_mean_absolute_error: 17.8551 - val_acc: 0.9239
Epoch 42/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 385.2419 - mean_absolute_error: 3.7377 - acc: 0.9276 - val_loss: 1129179.5000 - val_mean_absolute_error: 19.6634 - val_acc: 0.8849
Epoch 43/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 417.7102 - mean_absolute_error: 5.5412 - acc: 0.8893 - v

Epoch 78/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 395.5630 - mean_absolute_error: 4.2656 - acc: 0.9235 - val_loss: 1129167.3750 - val_mean_absolute_error: 19.9948 - val_acc: 0.8819
Epoch 79/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 433.3980 - mean_absolute_error: 5.8707 - acc: 0.8882 - val_loss: 1129323.2500 - val_mean_absolute_error: 16.8000 - val_acc: 0.9529
Epoch 80/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 374.7013 - mean_absolute_error: 2.6822 - acc: 0.9537 - val_loss: 1129831.6250 - val_mean_absolute_error: 19.8223 - val_acc: 0.8518
Epoch 81/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 428.0987 - mean_absolute_error: 5.8098 - acc: 0.8437 - val_loss: 1130013.7500 - val_mean_absolute_error: 21.7799 - val_acc: 0.7839
Epoch 82/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 491.7236 - mean_absolute_error: 7.7928 - acc: 0.7805 - v

16594/16594 [==============================] - 0s 3us/sample - loss: 376.3437 - mean_absolute_error: 1.7489 - acc: 0.9727 - val_loss: 1129975.1250 - val_mean_absolute_error: 20.3514 - val_acc: 0.8341
Epoch 117/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 435.3134 - mean_absolute_error: 6.2583 - acc: 0.8277 - val_loss: 1130057.1250 - val_mean_absolute_error: 21.5578 - val_acc: 0.7805
Epoch 118/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 476.2681 - mean_absolute_error: 7.5133 - acc: 0.7727 - val_loss: 1129717.3750 - val_mean_absolute_error: 18.0141 - val_acc: 0.8952
Epoch 119/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 397.6527 - mean_absolute_error: 3.9717 - acc: 0.8948 - val_loss: 1129223.7500 - val_mean_absolute_error: 18.7159 - val_acc: 0.8979
Epoch 120/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 391.5837 - mean_absolute_error: 4.5987 - acc: 0.9030 - val_loss: 11

Epoch 155/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 420.6325 - mean_absolute_error: 5.2931 - acc: 0.8620 - val_loss: 1129308.0000 - val_mean_absolute_error: 16.8033 - val_acc: 0.9481
Epoch 156/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 370.0098 - mean_absolute_error: 2.6845 - acc: 0.9505 - val_loss: 1129298.0000 - val_mean_absolute_error: 18.4607 - val_acc: 0.9164
Epoch 157/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 398.4543 - mean_absolute_error: 4.3064 - acc: 0.9177 - val_loss: 1129498.7500 - val_mean_absolute_error: 15.5798 - val_acc: 0.9853
Epoch 158/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 367.4093 - mean_absolute_error: 1.4129 - acc: 0.9816 - val_loss: 1129991.0000 - val_mean_absolute_error: 20.5784 - val_acc: 0.8214
Epoch 159/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 438.2237 - mean_absolute_error: 6.4951 - acc: 0.814

...

Epoch 19839/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 77.5757 - mean_absolute_error: 5.1119 - acc: 0.8633 - val_loss: 1131168.1250 - val_mean_absolute_error: 22.3961 - val_acc: 0.7665
Epoch 19840/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 153.1066 - mean_absolute_error: 7.8515 - acc: 0.7633 - val_loss: 1130976.7500 - val_mean_absolute_error: 18.9226 - val_acc: 0.8867
Epoch 19841/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 54.1320 - mean_absolute_error: 4.2822 - acc: 0.8818 - val_loss: 1130670.5000 - val_mean_absolute_error: 20.8307 - val_acc: 0.8812
Epoch 19842/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 102.8737 - mean_absolute_error: 6.0915 - acc: 0.8839 - val_loss: 1130622.8750 - val_mean_absolute_error: 23.4935 - val_acc: 0.8324
Epoch 19843/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 186.8350 - mean_absolute_error: 8.7417 - ac

Epoch 19877/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 63.2602 - mean_absolute_error: 4.6161 - acc: 0.8746 - val_loss: 1130740.8750 - val_mean_absolute_error: 20.3144 - val_acc: 0.8894
Epoch 19878/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 89.8693 - mean_absolute_error: 5.5637 - acc: 0.8963 - val_loss: 1130695.0000 - val_mean_absolute_error: 22.8537 - val_acc: 0.8460
Epoch 19879/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 169.0345 - mean_absolute_error: 8.0814 - acc: 0.8442 - val_loss: 1130752.7500 - val_mean_absolute_error: 19.1964 - val_acc: 0.9030
Epoch 19880/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 61.0436 - mean_absolute_error: 4.4254 - acc: 0.9116 - val_loss: 1131136.6250 - val_mean_absolute_error: 20.2889 - val_acc: 0.8450
Epoch 19881/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 91.2641 - mean_absolute_error: 5.6597 - acc:

Epoch 19915/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 181.4307 - mean_absolute_error: 8.4609 - acc: 0.8375 - val_loss: 1130697.2500 - val_mean_absolute_error: 19.4188 - val_acc: 0.9017
Epoch 19916/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 66.4662 - mean_absolute_error: 4.6756 - acc: 0.9081 - val_loss: 1131068.6250 - val_mean_absolute_error: 20.0418 - val_acc: 0.8525
Epoch 19917/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 84.1550 - mean_absolute_error: 5.4315 - acc: 0.8485 - val_loss: 1131281.2500 - val_mean_absolute_error: 22.5362 - val_acc: 0.7651
Epoch 19918/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 160.9797 - mean_absolute_error: 7.9779 - acc: 0.7622 - val_loss: 1131076.6250 - val_mean_absolute_error: 18.8405 - val_acc: 0.8925
Epoch 19919/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 56.4833 - mean_absolute_error: 4.1861 - acc

Epoch 19953/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 85.5422 - mean_absolute_error: 5.4655 - acc: 0.8450 - val_loss: 1131224.5000 - val_mean_absolute_error: 22.5636 - val_acc: 0.7624
Epoch 19954/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 163.9190 - mean_absolute_error: 8.0257 - acc: 0.7596 - val_loss: 1131061.6250 - val_mean_absolute_error: 18.9547 - val_acc: 0.8877
Epoch 19955/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 58.8212 - mean_absolute_error: 4.3155 - acc: 0.8841 - val_loss: 1130715.2500 - val_mean_absolute_error: 20.5056 - val_acc: 0.8843
Epoch 19956/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 93.5802 - mean_absolute_error: 5.7509 - acc: 0.8891 - val_loss: 1130660.3750 - val_mean_absolute_error: 23.0179 - val_acc: 0.8426
Epoch 19957/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 173.5824 - mean_absolute_error: 8.2486 - acc

Epoch 19991/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 52.5516 - mean_absolute_error: 4.0100 - acc: 0.8942 - val_loss: 1130500.8750 - val_mean_absolute_error: 20.7628 - val_acc: 0.8798
Epoch 19992/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 101.5836 - mean_absolute_error: 6.0529 - acc: 0.8838 - val_loss: 1130514.1250 - val_mean_absolute_error: 23.2878 - val_acc: 0.8375
Epoch 19993/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 184.7827 - mean_absolute_error: 8.5537 - acc: 0.8356 - val_loss: 1130505.3750 - val_mean_absolute_error: 19.5174 - val_acc: 0.8976
Epoch 19994/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 68.1507 - mean_absolute_error: 4.8001 - acc: 0.9055 - val_loss: 1130872.7500 - val_mean_absolute_error: 19.8840 - val_acc: 0.8566
Epoch 19995/20000
16594/16594 [==============================] - 0s 3us/sample - loss: 81.2331 - mean_absolute_error: 5.3057 - acc

In [28]:
model.save("rough_working_approx.h5")
#model = tf.keras.models.load_model("rough_working_approx.h5")

In [62]:
capital_tax = widgets.IntSlider(
    value=0.0,
    min=0.0,
    max=100.0,
    step=10.0,
    description='capital_tax:',
    continuous_update=False
)

In [63]:
labour_tax = widgets.IntSlider(
    value=0.0,
    min=0.0,
    max=100.0,
    step=10.0,
    description='labour_tax:',
    continuous_update=False
)

In [64]:
fig_util = go.FigureWidget(
            data=[dict(x=data_x[:, 0], 
                       y=data_x[:, 2], 
                       z=data_y[:, 0],
                       mode='markers', type='scatter3d')]
            )
fig_rev = go.FigureWidget(
            data=[dict(x=data_x[:, 0], 
                       y=data_x[:, 2], 
                       z=data_y[:, 1],
                       mode='markers', type='scatter3d')]
            )

In [65]:
def response_rev(change):
    grid = np.zeros((100, 3))
    grid[:, 1] = labour_tax.value / 100
    temp_grid = np.array(list(itertools.product(np.linspace(0,1, 10), np.linspace(0,1, 10))))
    grid[:, 0] = temp_grid[:, 0]
    grid[:, 2] = temp_grid[:, 1]


    results = model.predict(grid)
    with fig_rev.batch_update():
#            fig.data[0].x = grid[:, 0]
#            fig.data[0].y = x
#        results[:, 0] = labour_tax.value
        fig_rev.data[0].z = results[:, 1]

def response_util(change):
    grid = np.zeros((100, 3))
    grid[:, 1] = labour_tax.value / 100
    temp_grid = np.array(list(itertools.product(np.linspace(0,1, 10), np.linspace(0,1, 10))))
    grid[:, 0] = temp_grid[:, 0]
    grid[:, 2] = temp_grid[:, 1]


    results = model.predict(grid)
    with fig_util.batch_update():
#            fig.data[0].x = grid[:, 0]
#            fig.data[0].y = x
#        results[:, 0] = labour_tax.value
        fig_util.data[0].z = results[:, 0]


labour_tax.observe(response_rev, names="value")
labour_tax.observe(response_util, names="value")

In [66]:
cont1 = labour_tax

In [67]:
cont2 = widgets.HBox([fig_util, fig_rev])

In [68]:
widgets.VBox([cont1, 
              cont2])

In [69]:
fig_util.layout.title = 'Utility'
fig_rev.layout.title = 'Revenue'

In [70]:
fig_util.layout.scene.zaxis.range = [0, 100]
fig_rev.layout.scene.zaxis.range = [0, 100]

In [71]:
fig_util.layout.xaxis.autorange = False

In [151]:
data_y

array([[ 9.46823798, 48.96466   ],
       [14.07335084, 49.84570127],
       [42.29409792, 44.80442259],
       [60.17534714, 33.12087112],
       [45.95878138, 44.50526473],
       [15.90482802, 50.06513988],
       [72.04435663, 27.91236927],
       [56.84188231, 34.10722103],
       [32.02634699, 48.1510572 ],
       [69.4853922 , 22.88360764],
       [57.16259542, 33.83235438],
       [73.97688044, 18.78389566],
       [14.1535719 , 49.79004863],
       [43.91395512, 43.40697514],
       [84.38632828, 13.39453507],
       [30.95866458, 48.5669036 ],
       [51.47989641, 39.44148035],
       [52.2809331 , 38.60029236],
       [69.10992044, 23.44871355],
       [55.0913225 , 35.40955468],
       [74.0008944 , 27.67807185],
       [56.38024376, 37.68214366],
       [54.17568932, 36.44779493],
       [63.96644837, 31.08399825],
       [39.84757666, 46.12402625],
       [47.08282959, 41.17797553],
       [45.61979694, 46.36121111],
       [31.26443071, 48.50814456],
       [41.02268014,

In [52]:
fig.layout.M

In [15]:
import sys
print(sys.version)

3.6.8 |Anaconda custom (64-bit)| (default, Feb 21 2019, 18:30:04) [MSC v.1916 64 bit (AMD64)]


In [ ]:
152.4 % 1